In [9]:
import sympy as sp
from sympy import Piecewise, Array
from IPython.display import display

In [4]:
from sympy import Symbol, symbols
from sympy.core.numbers import Integer

# Method 2: Using symbols with assumptions
N,D,P = symbols('N D P', nonnegative=True, integer=True)

In [6]:
def F(N,D,P) :
    if N == 0 :
        return P
    elif D == 0:
        return F(N-1, 1, P)
    else:
        return P

In [7]:
F(N,D,P)

P

In [1]:
def g(n): 
    if n == 0 :
        return [(0,None), P]
    else:
        pass

In [12]:
Array([P,P]).subs(P,2)

[2, 2]

In [158]:
#  F(N=0, D,P) = P
# F(N>0, D=0, P) = F(N-1, D=1, P)
# F(N>0, D>0, P) = P/(2P+D) * max(F(N-1, D-1,P+1),F(N-1,D,P)) + (P+D)/(2P+D) * max(F(N-1,D+1,P),F(N-1,D,P)) 

# N=0 : 
# F(N,D,P) = P

# N=1:
# D=0: max(F(N-1,1,P), F(N-1,0,P)) # logically, I think F(N-1, 1, P) always wins?
# D>0: weighted sum of (higher of F(0,D-1,P+1),F(0,D-1,

# N=0
F0 = P

# N=1
# (D equality constraint or none, regional D-P constraints that must be positive, expected value)



from sympy import Poly, solve_rational_inequalities
inf = float('inf')

def poly_subs(poly, ptn = {}) :
    if not isinstance(poly, Poly) :
        return poly
    return Poly(poly.as_expr().subs(ptn))
def eqn_subs(eqn, ptn={}) :
    return (poly_subs(eqn[0], ptn), 
            poly_subs(eqn[1], ptn),
            eqn[2])

def F(n) :
        
    if n == 0 : 
        return {inf : [([(Poly(P), 0,'>='), (Poly(D), 0,'>=')], P)]}
    else :
        subproblems = F(n-1)
        select = lambda d: subproblems.get(d, subproblems.get(inf))
        
        ds = sorted(subproblems.keys())

        ret = {}
        ret[0] = select(1)
        for d in ds :
            take_minority = select(d)
            take_none = select(d+1)
            take_majority = select(d+2)

            take_minority = [ ([eqn_subs(e, {P: P+1, D: D-1}) for e in eqns], 
                               expr.subs({P: P+1, D: D-1})) for (eqns, expr) in take_minority]
            take_majority = [ ([eqn_subs(e, {D: D+1}) for e in eqns], 
                               expr.subs({D: D+1})) for (eqns, expr) in take_majority]

            return take_minority
            # take_minority = [[poly_subs(p, {P: P+1, D: D-1}) for p in e[0]], e[1].subs({P: P+1, D: D-1})) for e in take_minority]
            # take_minority = [[poly_subs(p, {D: D+1}), e[1].subs({D: D+1})) for p in e[0]] for e in take_majority]

            #take_minority = [(e[0].subs(P,P+1).subs(D,D-1), e[1].subs(P,P+1).subs(D,D-1)) for e in take_minority]
            #take_majority = [(e[0].subs(D,D+1), e[1].subs(D,D+1)) for e in take_majority]

            # DEBUG: ignore P-D regional info, take only the first region
            
            new_outcomes = []
            for A in take_minority :
                for B in take_none :
                    for C in take_majority :
                         for sign_min in [1,-1] :
                             for sign_maj in [1,-1] :

                                new_conditions = []
                                new_conditions += [(Poly(A[1]),Poly(B[1]), '>=' if sign_min == 1 else '<')]
                                new_conditions += [(Poly(B[1]),Poly(C[1]), '>=' if sign_maj == 1 else '<')]
                                # new_conditions += [B[1]-C[1]>=0 if sign_maj == 1 else B[1]-C[1] < 0]

                                if False in new_conditions:
                                    continue
                                new_conditions = [x for x in new_conditions if x != True]
                                new_conditions += A[0] + B[0] + C[0]

                                e = 0
                                e += P/(2*P+D) * {1 : A[1], -1: B[1]}[sign_min]
                                e += (P+D)/(2*P+D) * {1 : B[1], -1: C[1]}[sign_maj]
                                e = e.factor()
                                new_outcomes += [(Array(new_conditions), e)]
            ret[d+1] = new_outcomes

            
            
            #print(d, A,B,C, A[1]-B[1] < 0)
            # print(ret)
          
        
        return ret

F(0)



{inf: [([(Poly(P, P, domain='ZZ'), 0, '>='),
    (Poly(D, D, domain='ZZ'), 0, '>=')],
   P)]}

{inf: 2}

In [48]:
(P-P >= 0) == True

True

In [227]:
class Region :
    def __init__(self, constraints, expr) :
        self.constraints = constraints
        self.expr = expr
    def subs(self, ptn) :
        return Region(self.constraints, # [(poly_subs(a,ptn), poly_subs(b,ptn), c) for (a,b,c) in self.constraints],
                       self.expr.subs(ptn)
                     )
    def __eq__(self, other) :
        if not isinstance(other, Region):
            return False
        if self.expr != other.expr:
            return False

        pass
        
        return True
            
    def __repr__(self):
        return "Region"+str((self.constraints,self.expr))

def constraint_always(c) :
    try:
        return type(solve_rational_inequalities([[c]])) == sp.sets.fancysets.Reals
    except :
        return False
def constraint_never(c) :
    try:
        return type(solve_rational_inequalities([[c]])) == sp.sets.sets.EmptySet
    except:
        return False
def G(n) :
    """
    Return an object representing the expected payout of the game state (N=n, D, P),
    divided into different regions for different values of D and P.
    """

    # 
    if n == 0 :
        return {inf : [Region([((Poly(P),Poly(1,P)),'>='), ((Poly(D),Poly(1,D)),'>=')], P)]}
    else :
        subproblems = G(n-1)
        select_fn = lambda d: subproblems.get(d, subproblems.get(inf))

        ret = {}
        ret[0] = select_fn(1) # CASE FOR D==0
        
        for d in sorted(subproblems.keys()) : # CASE FOR D>0
            take_minority = select_fn(d)
            take_none = select_fn(d+1)
            take_majority = select_fn(d+2)

            take_minority = map(lambda e: e.subs({D:D-1, P:P+1}), take_minority)
            take_majority = map(lambda e: e.subs({D:D+1}), take_majority)

            new_outcomes = []
            for A in take_minority :
                for B in take_none :
                    for C in take_majority :
                         for sign_min in [1,-1] :
                             for sign_maj in [1,-1] :
                                new_conditions = []
                                new_conditions += [((Poly(A.expr)-Poly(B.expr), Poly(1,(P,D))), '>=' if sign_min == 1 else '<')]
                                new_conditions += [((Poly(B.expr)-Poly(C.expr), Poly(1,(P,D))), '>=' if sign_maj == 1 else '<')]

                                #if False in new_conditions:
                                if any([constraint_never(x) for x in new_conditions]):
                                    continue
                                new_conditions = [x for x in new_conditions if x != True]
                                new_conditions += A.constraints + B.constraints + C.constraints

                                new_constraints = [x for x in new_conditions if not constraint_always(x)]
                                 
                                e = 0
                                e += P/(2*P+D) * {1 : A.expr, -1: B.expr}[sign_min]
                                e += (P+D)/(2*P+D) * {1 : B.expr, -1: C.expr}[sign_maj]
                                e = e.factor()
                                new_outcomes += [Region(new_conditions, e)]
            ret[d+1] = new_outcomes
            
            #print(d, take_minority, take_none, take_majority)
            
        return ret






In [228]:
G(2)

ALWAYS [((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>=')]
ALWAYS [((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>=')]
ALWAYS [((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>=')]
ALWAYS [((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>=')]
ALWAYS [((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, do

{0: [Region([((Poly(1, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(P, P, domain='ZZ'), Poly(1, P, domain='ZZ')), '>='), ((Poly(D, D, domain='ZZ'), Poly(1, D, domain='ZZ')), '>='), ((Poly(P, P, domain='ZZ'), Poly(1, P, domain='ZZ')), '>='), ((Poly(D, D, domain='ZZ'), Poly(1, D, domain='ZZ')), '>='), ((Poly(P, P, domain='ZZ'), Poly(1, P, domain='ZZ')), '>='), ((Poly(D, D, domain='ZZ'), Poly(1, D, domain='ZZ')), '>=')], P*(D + 2*P + 1)/(D + 2*P))],
 1: [Region([((Poly(-(1/(D + 2*P))*D*P - 2*(1/(D + 2*P))*P**2 - (1/(D + 2*P))*P + P + 1, 1/(D + 2*P), D, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly((1/(D + 2*P))*D*P + 2*(1/(D + 2*P))*P**2 + (1/(D + 2*P))*P - (1/(D + 2*P + 1))*D*P - 2*(1/(D + 2*P + 1))*P**2 - 2*(1/(D + 2*P + 1))*P, 1/(D + 2*P), 1/(D + 2*P + 1), D, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>='), ((Poly(P, P, domain='ZZ'), Poly(1, P, domain='ZZ')), '>='), ((Poly(D, D, domain='ZZ')

In [226]:
x = symbols('x')
solve_rational_inequalities([[

((Poly(-x + 1), Poly(1, x)), '>='),

((Poly(-x + 1), Poly(1, x)), '<=')]])

solve_rational_inequalities([[
((Poly(P), Poly(4,P)), '>=')]])

solve_rational_inequalities([[
((Poly(P-2), Poly(P)), '>')]])

type(solve_rational_inequalities([[
((Poly(0, P, domain='ZZ'), Poly(1, P, D, domain='ZZ')), '>=')]]))

sympy.sets.fancysets.Reals

In [214]:
sp.sets.fancysets.Reals

sympy.sets.fancysets.Reals